In [ ]:
import pandas as pd
import numpy as np
import datetime
from collections import Counter
from sklearn.metrics.pairwise import cosine_similarity

: 

In [106]:
movies_data = pd.read_csv('movies.csv') 
ratings_data = pd.read_csv('ratings.csv')

In [ ]:
print(ratings_data)

In [107]:
print(movies_data.shape)
print(ratings_data.shape)

(9742, 3)
(100836, 4)


In [108]:
genome_scores_data = pd.read_csv('genome-scores.csv') 

In [109]:
scores_pivot = genome_scores_data.pivot_table(index = ["movieId"],columns = ["tagId"],values = "relevance").reset_index()
scores_pivot.head()

tagId  movieId        1        2        3        4        5        6        7  \
0            1  0.02875  0.02375  0.06250  0.07575  0.14075  0.14675  0.06350   
1            2  0.04125  0.04050  0.06275  0.08275  0.09100  0.06125  0.06925   
2            3  0.04675  0.05550  0.02925  0.08700  0.04750  0.04775  0.04600   
3            4  0.03425  0.03800  0.04050  0.03100  0.06500  0.03575  0.02900   
4            5  0.04300  0.05325  0.03800  0.04100  0.05400  0.06725  0.02775   

tagId        8       9  ...     1119     1120     1121     1122     1123  \
0      0.20375  0.2020  ...  0.04050  0.01425  0.03050  0.03500  0.14125   
1      0.09600  0.0765  ...  0.05250  0.01575  0.01250  0.02000  0.12225   
2      0.14275  0.0285  ...  0.06275  0.01950  0.02225  0.02300  0.12200   
3      0.08650  0.0320  ...  0.05325  0.02800  0.01675  0.03875  0.18200   
4      0.07650  0.0215  ...  0.05350  0.02050  0.01425  0.02550  0.19225   

tagId     1124     1125     1126     1127     1128  
0      0.05775  0.03900  0.02975  0.08475  0.02200  
1      0.03275  0.02100  0.01100  0.10525  0.01975  
2      0.03475  0.01700  0.01800  0.09100  0.01775  
3      0.07050  0.01625  0.01425  0.08850  0.01500  
4      0.02675  0.01625  0.01300  0.08700  0.01600  

[5 rows x 1129 columns]

In [110]:
#join
mov_tag_df = movies_data.merge(scores_pivot, left_on='movieId', right_on='movieId', how='left')
mov_tag_df = mov_tag_df.fillna(0) 
mov_tag_df = mov_tag_df.drop(['title','genres'], axis = 1)
mov_tag_df.head()

movieId        1        2        3        4        5        6        7  \
0        1  0.02875  0.02375  0.06250  0.07575  0.14075  0.14675  0.06350   
1        2  0.04125  0.04050  0.06275  0.08275  0.09100  0.06125  0.06925   
2        3  0.04675  0.05550  0.02925  0.08700  0.04750  0.04775  0.04600   
3        4  0.03425  0.03800  0.04050  0.03100  0.06500  0.03575  0.02900   
4        5  0.04300  0.05325  0.03800  0.04100  0.05400  0.06725  0.02775   

         8       9  ...     1119     1120     1121     1122     1123     1124  \
0  0.20375  0.2020  ...  0.04050  0.01425  0.03050  0.03500  0.14125  0.05775   
1  0.09600  0.0765  ...  0.05250  0.01575  0.01250  0.02000  0.12225  0.03275   
2  0.14275  0.0285  ...  0.06275  0.01950  0.02225  0.02300  0.12200  0.03475   
3  0.08650  0.0320  ...  0.05325  0.02800  0.01675  0.03875  0.18200  0.07050   
4  0.07650  0.0215  ...  0.05350  0.02050  0.01425  0.02550  0.19225  0.02675   

      1125     1126     1127     1128  
0  0.03900  0.02975  0.08475  0.02200  
1  0.02100  0.01100  0.10525  0.01975  
2  0.01700  0.01800  0.09100  0.01775  
3  0.01625  0.01425  0.08850  0.01500  
4  0.01625  0.01300  0.08700  0.01600  

[5 rows x 1129 columns]

In [111]:
def set_genres(genres,col):
    if genres in col.split('|'): return 1
    else: return 0

In [112]:
mov_genres_df = pd.read_csv('movies.csv') 
mov_genres_df.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [113]:
mov_genres_df["Action"] = mov_genres_df.apply(lambda x: set_genres("Action",x['genres']), axis=1)
mov_genres_df["Adventure"] = mov_genres_df.apply(lambda x: set_genres("Adventure",x['genres']), axis=1)
mov_genres_df["Animation"] = mov_genres_df.apply(lambda x: set_genres("Animation",x['genres']), axis=1)
mov_genres_df["Children"] = mov_genres_df.apply(lambda x: set_genres("Children",x['genres']), axis=1)
mov_genres_df["Comedy"] = mov_genres_df.apply(lambda x: set_genres("Comedy",x['genres']), axis=1)
mov_genres_df["Crime"] = mov_genres_df.apply(lambda x: set_genres("Crime",x['genres']), axis=1)
mov_genres_df["Documentary"] = mov_genres_df.apply(lambda x: set_genres("Documentary",x['genres']), axis=1)
mov_genres_df["Drama"] = mov_genres_df.apply(lambda x: set_genres("Drama",x['genres']), axis=1)
mov_genres_df["Fantasy"] = mov_genres_df.apply(lambda x: set_genres("Fantasy",x['genres']), axis=1)
mov_genres_df["Film-Noir"] = mov_genres_df.apply(lambda x: set_genres("Film-Noir",x['genres']), axis=1)
mov_genres_df["Horror"] = mov_genres_df.apply(lambda x: set_genres("Horror",x['genres']), axis=1)
mov_genres_df["Musical"] = mov_genres_df.apply(lambda x: set_genres("Musical",x['genres']), axis=1)
mov_genres_df["Mystery"] = mov_genres_df.apply(lambda x: set_genres("Mystery",x['genres']), axis=1)
mov_genres_df["Romance"] = mov_genres_df.apply(lambda x: set_genres("Romance",x['genres']), axis=1)
mov_genres_df["Sci-Fi"] = mov_genres_df.apply(lambda x: set_genres("Sci-Fi",x['genres']), axis=1)
mov_genres_df["Thriller"] = mov_genres_df.apply(lambda x: set_genres("Thriller",x['genres']), axis=1)
mov_genres_df["War"] = mov_genres_df.apply(lambda x: set_genres("War",x['genres']), axis=1)
mov_genres_df["Western"] = mov_genres_df.apply(lambda x: set_genres("Western",x['genres']), axis=1)
mov_genres_df["(no genres listed)"] = mov_genres_df.apply(lambda x: set_genres("(no genres listed)",x['genres']), axis=1)

In [114]:
mov_genres_df.drop(['title','genres'], axis = 1, inplace=True)
mov_genres_df.head()

movieId  Action  Adventure  Animation  Children  Comedy  Crime  \
0        1       0          1          1         1       1      0   
1        2       0          1          0         1       0      0   
2        3       0          0          0         0       1      0   
3        4       0          0          0         0       1      0   
4        5       0          0          0         0       1      0   

   Documentary  Drama  Fantasy  Film-Noir  Horror  Musical  Mystery  Romance  \
0            0      0        1          0       0        0        0        0   
1            0      0        1          0       0        0        0        0   
2            0      0        0          0       0        0        0        1   
3            0      1        0          0       0        0        0        1   
4            0      0        0          0       0        0        0        0   

   Sci-Fi  Thriller  War  Western  (no genres listed)  
0       0         0    0        0                   0  
1       0         0    0        0                   0  
2       0         0    0        0                   0  
3       0         0    0        0                   0  
4       0         0    0        0                   0

In [115]:
movies = pd.read_csv('movies.csv') 

In [116]:
def set_year(title):
    year = title.strip()[-5:-1]
    if year.isnumeric() == True: return int(year)
    else: return 1800
#add year field
movies_data['year'] = movies_data.apply(lambda x: set_year(x['title']), axis=1)
movies = movies_data.drop('genres', axis = 1)
movies.head()

movieId                               title  year
0        1                    Toy Story (1995)  1995
1        2                      Jumanji (1995)  1995
2        3             Grumpier Old Men (1995)  1995
3        4            Waiting to Exhale (1995)  1995
4        5  Father of the Bride Part II (1995)  1995

In [117]:
#define function to group years
def set_year_group(year):
    if (year < 1900): return 0
    elif (1900 <= year <= 1975): return 1
    elif (1976 <= year <= 1995): return 2
    elif (1996 <= year <= 2003): return 3
    elif (2004 <= year <= 2009): return 4
    elif (2010 <= year): return 5
    else: return 0
movies['year_group'] = movies.apply(lambda x: set_year_group(x['year']), axis=1)
#no need title and year fields
movies.drop(['title','year'], axis = 1, inplace=True)

In [118]:
agg_movies_rat = ratings_data.groupby(['movieId']).agg({'rating': [np.size, np.mean]}).reset_index()
agg_movies_rat.columns = ['movieId','rating_counts', 'rating_mean']
agg_movies_rat.head()

movieId  rating_counts  rating_mean
0        1            215     3.920930
1        2            110     3.431818
2        3             52     3.259615
3        4              7     2.357143
4        5             49     3.071429

In [119]:
#define function to group rating counts
def set_rating_group(rating_counts):
    if (rating_counts <= 1): return 0
    elif (2 <= rating_counts <= 10): return 1
    elif (11 <= rating_counts <= 100): return 2
    elif (101 <= rating_counts <= 1000): return 3
    elif (1001 <= rating_counts <= 5000): return 4
    elif (5001 <= rating_counts): return 5
    else: return 0
agg_movies_rat['rating_group'] = agg_movies_rat.apply(lambda x: set_rating_group(x['rating_counts']), axis=1)
#no need rating_counts field
agg_movies_rat.drop('rating_counts', axis = 1, inplace=True)
mov_rating_df = movies.merge(agg_movies_rat, left_on='movieId', right_on='movieId', how='left')
mov_rating_df = mov_rating_df.fillna(0)
mov_rating_df.head()

movieId  year_group  rating_mean  rating_group
0        1           2     3.920930           3.0
1        2           2     3.431818           3.0
2        3           2     3.259615           2.0
3        4           2     2.357143           1.0
4        5           2     3.071429           2.0

In [120]:
mov_tag_df = mov_tag_df.set_index('movieId')
mov_genres_df = mov_genres_df.set_index('movieId')
mov_rating_df = mov_rating_df.set_index('movieId')

In [121]:
#cosine similarity for mov_tag_df
cos_tag = cosine_similarity(mov_tag_df.values)*0.5
#cosine similarity for mov_genres_df
cos_genres = cosine_similarity(mov_genres_df.values)*0.25
#cosine similarity for mov_rating_df
cos_rating = cosine_similarity(mov_rating_df.values)*0.25
#mix
cos = cos_tag+cos_genres+cos_rating

In [122]:
cols = mov_tag_df.index.values
inx = mov_tag_df.index
movies_sim = pd.DataFrame(cos, columns=cols, index=inx)
movies_sim.head()

1         2         3         4         5         6         7       \
movieId                                                                         
1        1.000000  0.831171  0.671888  0.621701  0.684143  0.560833  0.653112   
2        0.831171  1.000000  0.586454  0.555409  0.572422  0.509135  0.571354   
3        0.671888  0.586454  1.000000  0.823610  0.853155  0.564434  0.886428   
4        0.621701  0.555409  0.823610  1.000000  0.758331  0.538576  0.851611   
5        0.684143  0.572422  0.853155  0.758331  1.000000  0.509864  0.803361   

           8         9         10      ...    193565    193567    193571  \
movieId                                ...                                 
1        0.738648  0.513073  0.633484  ...  0.294232  0.254226  0.267313   
2        0.817328  0.558653  0.667859  ...  0.181132  0.174812  0.186109   
3        0.600316  0.565501  0.583471  ...  0.291585  0.196495  0.333426   
4        0.628123  0.538959  0.535301  ...  0.302253  0.327340  0.437597   
5        0.575341  0.534352  0.542106  ...  0.328564  0.197301  0.385168   

           193573    193579    193581    193583    193585    193587    193609  
movieId                                                                        
1        0.300059  0.182429  0.355961  0.376078  0.182429  0.261486  0.318377  
2        0.186109  0.181132  0.258278  0.264466  0.181132  0.181132  0.199085  
3        0.208426  0.203197  0.296815  0.305259  0.203197  0.203197  0.397479  
4        0.233473  0.230085  0.305642  0.313418  0.374422  0.230085  0.375386  
5        0.208392  0.203564  0.333392  0.347901  0.203564  0.203564  0.468041  

[5 rows x 9742 columns]

In [123]:
def get_similar(movieId):
    df = movies_sim.loc[movies_sim.index == movieId].reset_index(). \
            melt(id_vars='movieId', var_name='sim_moveId', value_name='relevance'). \
            sort_values('relevance', axis=0, ascending=False)[1:6]
    return df
#create empty df
movies_similarity = pd.DataFrame(columns=['movieId','sim_moveId','relevance'])

In [124]:
for x in movies_sim.index.tolist():
    movies_similarity = movies_similarity.append(get_similar(x))
movies_similarity.head()

C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\276479794.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_similarity = movies_similarity.append(get_similar(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\276479794.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_similarity = movies_similarity.append(get_similar(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\276479794.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_similarity = movies_similarity.append(get_similar(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\276479794.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_simila

movieId sim_moveId  relevance
3568       1       4886   0.974686
2355       1       3114   0.967164
7355       1      78499   0.937822
1757       1       2355   0.936678
4360       1       6377   0.934974

Later

In [125]:
users_df = pd.DataFrame(ratings_data['userId'].unique(), columns=['userId'])
users_df.head()

userId
0       1
1       2
2       3
3       4
4       5

In [126]:
#create movies_df
movies_df = movies_data.drop('genres', axis = 1)
#calculate mean of ratings for each movies
agg_rating_avg = ratings_data.groupby(['movieId']).agg({'rating': np.mean}).reset_index()
agg_rating_avg.columns = ['movieId', 'rating_mean']
#merge
movies_df = movies_df.merge(agg_rating_avg, left_on='movieId', right_on='movieId', how='left')
movies_df.head()

movieId                               title  year  rating_mean
0        1                    Toy Story (1995)  1995     3.920930
1        2                      Jumanji (1995)  1995     3.431818
2        3             Grumpier Old Men (1995)  1995     3.259615
3        4            Waiting to Exhale (1995)  1995     2.357143
4        5  Father of the Bride Part II (1995)  1995     3.071429

In [127]:
genres = [
    "Action",
    "Adventure",
    "Animation",
    "Children",
    "Comedy",
    "Crime",
    "Documentary",
    "Drama",
    "Fantasy",
    "Film-Noir",
    "Horror",
    "Musical",
    "Mystery",
    "Romance",
    "Sci-Fi",
    "Thriller",
    "War",
    "Western",
    "(no genres listed)"]
genres_df = pd.DataFrame(genres, columns=['genres'])
genres_df.head()

genres
0     Action
1  Adventure
2  Animation
3   Children
4     Comedy

In [128]:
users_movies_df = ratings_data.drop('timestamp', axis = 1)
users_movies_df.head()

userId  movieId  rating
0       1        1     4.0
1       1        3     4.0
2       1        6     4.0
3       1       47     5.0
4       1       50     5.0

In [129]:
movies_genres_df = movies_data.drop('title', axis = 1)

In [130]:
def get_movie_genres(movieId):
    movie = movies_genres_df[movies_genres_df['movieId']==movieId]
    genres = movie['genres'].tolist()
    df = pd.DataFrame([b for a in [i.split('|') for i in genres] for b in a], columns=['genres'])
    df.insert(loc=0, column='movieId', value=movieId)
    return df

In [131]:
movies_genres=pd.DataFrame(columns=['movieId','genres'])
for x in movies_genres_df['movieId'].tolist():
    movies_genres=movies_genres.append(get_movie_genres(x))
movies_genres.head()

C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\732023539.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_genres=movies_genres.append(get_movie_genres(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\732023539.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_genres=movies_genres.append(get_movie_genres(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\732023539.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_genres=movies_genres.append(get_movie_genres(x))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\732023539.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  movies_genres=movies_genres.

movieId     genres
0       1  Adventure
1       1  Animation
2       1   Children
3       1     Comedy
4       1    Fantasy

In [132]:
#join to movies data to get genre information
user_genres_df = ratings_data.merge(movies_data, left_on='movieId', right_on='movieId', how='left')
#drop columns that will not be used
user_genres_df.drop(['movieId','rating','timestamp','title'], axis = 1, inplace=True)
user_genres_df.head()

userId                                       genres  year
0       1  Adventure|Animation|Children|Comedy|Fantasy  1995
1       1                               Comedy|Romance  1995
2       1                        Action|Crime|Thriller  1995
3       1                             Mystery|Thriller  1995
4       1                       Crime|Mystery|Thriller  1995

In [133]:
def get_favorite_genre(userId):
    user = user_genres_df[user_genres_df['userId']==userId]
    genres = user['genres'].tolist()
    movie_list = [b for a in [i.split('|') for i in genres] for b in a]
    counter = Counter(movie_list)
    return counter.most_common(1)[0][0]

In [134]:
#create empty df
users_genres = pd.DataFrame(columns=['userId','genre'])
for x in users_df['userId'].tolist():
    users_genres = users_genres.append(pd.DataFrame([[x,get_favorite_genre(x)]], columns=['userId','genre']))
users_genres.head()

C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\2600934114.py:4: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  users_genres = users_genres.append(pd.DataFrame([[x,get_favorite_genre(x)]], columns=['userId','genre']))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\2600934114.py:4: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  users_genres = users_genres.append(pd.DataFrame([[x,get_favorite_genre(x)]], columns=['userId','genre']))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\2600934114.py:4: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  users_genres = users_genres.append(pd.DataFrame([[x,get_favorite_genre(x)]], columns=['userId','genre']))
C:\Users\amogh\AppData\Local\Temp\ipykernel_20568\2600934114.py:4: FutureWar

userId   genre
0      1  Action
0      2   Drama
0      3   Drama
0      4   Drama
0      5   Drama

In [ ]:
users_df.to_csv('users.csv', sep='|', header=True, index=False)
movies_df.to_csv('movies.csv', sep='|', header=True, index=False)
genres_df.to_csv('genres.csv', sep='|', header=True, index=False)
users_movies_df.to_csv('users_movies.csv', sep='|', header=True, index=False)
movies_genres.to_csv('movies_genres.csv', sep='|', header=True, index=False)
users_genres.to_csv('users_genres.csv', sep='|', header=True, index=False)
movies_similarity.to_csv('movies_similarity.csv', sep='|', header=True, index=False)